Практикум 1. Поиск в PDB и основы визуализации.

Задание 1.

In [10]:
!pip install nglview  --user


/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [42]:
import nglview as nv
import requests         # Этот стандартный модуль позволяет посылать запросы к веб-ресурсам
import json             # Этот стандартный модуль позволяет легко работать с текстовым форматом json

In [43]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

In [44]:
keyword_clause = {
    "type": "terminal",
    "service": "full_text", 
    "parameters": {
        "value": "paracetamol"
    }
}

my_query["query"]["nodes"].append(keyword_clause)

In [45]:
resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.7,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [46]:
has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 1,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [47]:
date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2010-01-01",
            "to": "2015-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [48]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query) 

search = requests.post(f'{rcsb}', data=json_query) # Отсылаем запрос

search_result = search.json() # Распаковываем ответ сервера в словарь
search_result

{'query_id': '36d696a9-d213-4573-862e-5a69bee9a129',
 'result_type': 'entry',
 'total_count': 10,
 'result_set': [{'identifier': '4A9J',
   'score': 1.0,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 16183, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 17160, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 20713, 'original_score': 1.0, 'norm_score': 1.0}]},
    {'service_type': 'full_text',
     'nodes': [{'node_id': 9168,
       'original_score': 16.94811248779297,
       'norm_score': 1.0}]}]},
  {'identifier': '3PY4',
   'score': 0.9937960634599496,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 16183, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 17160, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 20713, 'original_score': 1.0, 'norm_score': 1.0}]},
    {'service_type': 'full_text',
     'nodes': [{'node_id': 9168,
       'original_score': 16.754962921142578,
       'norm_score': 0.

In [49]:
best_hit = search_result["result_set"][0] # Лучшая находка
best_hit

{'identifier': '4A9J',
 'score': 1.0,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 16183, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 17160, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 20713, 'original_score': 1.0, 'norm_score': 1.0}]},
  {'service_type': 'full_text',
   'nodes': [{'node_id': 9168,
     'original_score': 16.94811248779297,
     'norm_score': 1.0}]}]}

In [50]:
view = nv.show_pdbid('4A9J') 
view

NGLWidget()

Задание 2. 

По идентификатору 4A9J найдена запись о бромодомене BRD2 человека. Ключевое слово paracetamol действительно встречается в статье, связанной с записью. Парацетамол входит в набор фрагментов, с помощью скрининга которых создаются главные молекулы для BET бромодоменов. Определенные фрагменты (включая парацетамол) последовательно связываются с различными бромодоменами, такими как CREBBP, что указывает на их способность действовать как общие бромодоменовые шаблоны.

Задание 3.

In [51]:
from ipywidgets import interact, fixed

In [52]:
representations = [
  'ball+stick',      # шаростержневая модель
  'backbone',        # прямые линии, соединяющие С-альфа атомы
  'cartoon',         # условное отображение вторичной структуры
  'helixorient',     # упрощенное отображение 
  'hyperball',       # сглаженная шаростержневая модель
  'licorice',        # стержневая модель (без шаров)
  'line',            # очень тонкая стержневая модель
  'point',           # атомы в виде плоских точек
  'ribbon',          # отображение остова в виде ленты
  'rocket',          # отображение альфа-спиралей как цилиндров
  'rope',            # отображение остова в виде колбасы
  'spacefill',       # атомы в виде шаров соотв. Ван-дер-Ваальсова радиуса
  'surface',         # поверхность
  'trace',           # сглаженная линия, соединяющая С-альфа атомы
  'tube'             # более сдержанный rope
]

In [53]:
colors = [
  'random',
  'uniform',
  'atomindex',      # от синего к красному с ростом номера атома
  'residueindex',   # от синего к красному с ростом номера остатка
  'chainindex',     # каждой цепи свой цвет
  'sstruc',         # стандартные цвета для типа вторичной структуры
  'element',        # стандартные цвета для химических элементов
  'resname',        # свой цвет каждому из 20 остатков
  'bfactor',        # чем темнее, тем подвижнее
  'hydrophobicity', # чем темнее, тем гидрофобнее
]

In [54]:
my_examples = {
    'Example 1': {
        'description': '''
Вариант 1.
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок в виде rope красного цвета
Боковые радикалы в стержневой модели, покрашенные согласно элементу
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам
''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white',
                    'opacity': 0.1
                 }
            },
            {
                'type': 'rope',
                'params': {
                    'sele': 'protein',                 
                    'color': 'red'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',
                    'color' :'element'
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                 }
            },
           
        ],
    },
    'Example 6': {
        'description': '''
Вариант 6.
Белок в виде cartoon темно-серого цвета
Боковые радикалы в виде линий светло-серого цвета
Боковые радикалы полярных аминокислот в виде hyperball, покрашены по элементам
Лиганды в шаростержневой модели, покрашены по элементам, углероды покрашены в темно-синий
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'darkgray'
                 }
            },
            {
                'type': 'line',
                'params': {
                    'sele': 'sidechainAttached',                 
                    'color': 'lightgrey'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'polar and sidechainAttached',
                    'color' :'element'
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand and _C',               
                    'color': 'darkblue'  
                 }
            },
           
        ],
    },
    'Example 10': {
        'description': '''
Вариант 10.
Белок в виде cartoon белого цвета
Cartoon для остатков с 20-го по 55-й покрашен в зеленый
Для остатков с 20-го по 55-й показаны боковые радикалы в модели hyperball, покраска по элементам
Лиганды показаны в шаростержневой модели, покраска по элементам
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'white'  
                 }
            },
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein and 20-55',                     
                    'color': 'green'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'sidechainAttached and 20-55',
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',
                'params': {
                    'sele': 'ligand',                     
                    'color': 'element'  
                 }
            },
        ],
    },
}


In [55]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("4A9J", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 1', 'Example 6', 'Example 10'), v…

NGLWidget()